In [3]:
import pandas as pd
import numpy as np
import optuna
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.metrics import (
    accuracy_score,
    f1_score,
    classification_report,
    confusion_matrix,
)
import lightgbm as lgb
import joblib
import matplotlib.pyplot as plt
import seaborn as sns

# Chargement des données
df = pd.read_csv("./data/train_data.csv")
# Suppression de Surname

# Suppression des outliers pour la colonne Age
Q1 = df["Age"].quantile(0.25)
Q3 = df["Age"].quantile(0.75)
IQR = Q3 - Q1
lower_bound = Q1 - 1.5 * IQR
upper_bound = Q3 + 1.5 * IQR
df = df[(df["Age"] >= lower_bound) & (df["Age"] <= upper_bound)]

# Définition des variables continues et catégoriques
continuous_features = ["Age", "Balance"]
categorical_cols = ["Geography", "Gender"]

# Encodage des variables catégorielles
encoder = OneHotEncoder(sparse_output=False, drop="first")
encoded_data = encoder.fit_transform(df[categorical_cols])
encoded_df = pd.DataFrame(
    encoded_data, columns=encoder.get_feature_names_out(categorical_cols)
)

# Fusionner avec le dataset et supprimer les anciennes colonnes
df = df.drop(columns=categorical_cols).reset_index(drop=True)
df = pd.concat([df, encoded_df], axis=1)

# Feature Engineering
df["HasBalance"] = (df["Balance"] > 0).astype(int)
df["AgeByBalance"] = df["Age"] * df["Balance"]
df["BalanceMinusEstimatedSalary"] = df["Balance"] - df["EstimatedSalary"]
df["BalanceToSalaryRatio"] = df["Balance"] / (df["EstimatedSalary"] + 1)
df["AgeByProducts"] = df["Age"] * df["NumOfProducts"]
df["IsHighBalance"] = (df["Balance"] > df["Balance"].median()).astype(int)
df["IsSenior"] = df["Age"].apply(lambda x: 1 if x >= 60 else 0)
df["IsActive_by_CreditCard"] = df["HasCrCard"] * df["IsActiveMember"]
df["Products_Per_Tenure"] = df["Tenure"] / df["NumOfProducts"]
df["AgeCat"] = np.round(df.Age / 20).astype("int").astype("category")

# Suppression des colonnes inutiles
df = df.drop(
    columns=["CustomerId", "Surname", "ID", "Tenure", "CreditScore", "EstimatedSalary"]
)

# Normalisation des variables numériques
numeric_cols = ["Age", "Balance"]
scaler = StandardScaler()
df[numeric_cols] = scaler.fit_transform(df[numeric_cols])

# Sauvegarde du scaler
joblib.dump(scaler, "scaler.pkl")

# Définition des features et cible
X = df.drop(columns=["Exited"])
y = df["Exited"]

# Chargement et prétraitement du test set
df_test = pd.read_csv("./data/test_data.csv")
df_test = df_test[(df_test["Age"] >= lower_bound) & (df_test["Age"] <= upper_bound)]
df_test_encoded = encoder.transform(df_test[categorical_cols])
df_test_encoded_df = pd.DataFrame(
    df_test_encoded, columns=encoder.get_feature_names_out(categorical_cols)
)
df_test = df_test.drop(columns=categorical_cols).reset_index(drop=True)
df_test = pd.concat([df_test, df_test_encoded_df], axis=1)
df_test[numeric_cols] = scaler.transform(df_test[numeric_cols])


# Définition de la fonction Optuna
def objective(trial):
    params = {
        "objective": "binary",
        "metric": "binary_logloss",
        "max_depth": trial.suggest_int("max_depth", 3, 15),
        "num_leaves": trial.suggest_int("num_leaves", 20, 200),
        "min_child_samples": trial.suggest_int("min_child_samples", 5, 200),
        "subsample": trial.suggest_float("subsample", 0.3, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.3, 1.0),
        "learning_rate": trial.suggest_loguniform("learning_rate", 0.0001, 0.1),
        "n_estimators": trial.suggest_int("n_estimators", 100, 1000),
        "reg_alpha": trial.suggest_loguniform("reg_alpha", 0.01, 10.0),
        "reg_lambda": trial.suggest_loguniform("reg_lambda", 0.01, 10.0),
        "random_state": 42,
        "is_unbalance": True,
    }

    skf = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)
    f1_scores = []

    for fold, (train_idx, val_idx) in enumerate(skf.split(X, y), 1):
        X_train, X_val = X.iloc[train_idx], X.iloc[val_idx]
        y_train, y_val = y.iloc[train_idx], y.iloc[val_idx]

        model = lgb.LGBMClassifier(**params)
        model.fit(X_train, y_train)
        y_pred_proba = model.predict_proba(X_val)[:, 1]
        y_pred = (y_pred_proba >= 0.60).astype(int)  # Ajustement du seuil à 0.35
        f1 = f1_score(y_val, y_pred)
        f1_scores.append(f1)
        print(f"Fold {fold} - F1-score: {f1:.4f}")

    return np.mean(f1_scores)


# Optimisation avec Optuna
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

# Entraînement final avec les meilleurs hyperparamètres
best_params = study.best_params
lgbm_model = lgb.LGBMClassifier(**best_params)
lgbm_model.fit(X, y)
joblib.dump(lgbm_model, "lgbm_optimized.pkl")
print("✅ Modèle optimisé sauvegardé")

# Prédiction sur le test set
df_test_input = df_test[X.columns]
y_test_pred = lgbm_model.predict(df_test_input)

# Génération du fichier de soumission
submission = pd.DataFrame({"ID": df_test["ID"], "Exited": y_test_pred})
submission.to_csv("submission.csv", index=False)
print("✅ Submission sauvegardée")

[I 2025-02-06 23:11:06,444] A new study created in memory with name: no-name-55daa123-ac8a-448c-97b7-1ec5b76e2ada
/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:95: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  "learning_rate": trial.suggest_loguniform("learning_rate", 0.0001, 0.1),
/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:97: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  "reg_alpha": trial.suggest_loguniform("reg_alpha", 0.01, 10.0),
/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:98: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be 

[LightGBM] [Info] Number of positive: 25492, number of negative: 98682
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001833 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1235
[LightGBM] [Info] Number of data points in the train set: 124174, number of used features: 17
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.205293 -> initscore=-1.353538
[LightGBM] [Info] Start training from score -1.353538
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[I 2025-02-06 23:12:50,068] Trial 0 finished with value: 0.6514728395460652 and parameters: {'max_depth': 8, 'num_leaves': 163, 'min_child_samples': 11, 'subsample': 0.3120689962143454, 'colsample_bytree': 0.4586153483525721, 'learning_rate': 0.025161030882402867, 'n_estimators': 871, 'reg_alpha': 0.2563434496460093, 'reg_lambda': 0.26360864798395983}. Best is trial 0 with value: 0.6514728395460652.


Fold 10 - F1-score: 0.6570


/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:95: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  "learning_rate": trial.suggest_loguniform("learning_rate", 0.0001, 0.1),
/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:97: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  "reg_alpha": trial.suggest_loguniform("reg_alpha", 0.01, 10.0),
/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:98: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) inst

...

/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:95: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  "learning_rate": trial.suggest_loguniform("learning_rate", 0.0001, 0.1),
/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:97: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  "reg_alpha": trial.suggest_loguniform("reg_alpha", 0.01, 10.0),
/var/folders/vl/5_gvvsdd2lgfkdcbt1df_nxh0000gn/T/ipykernel_48809/2568369162.py:98: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) inst

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001912 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1235
[LightGBM] [Info] Number of data points in the train set: 124174, number of used features: 17
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.205293 -> initscore=-1.353538
[LightGBM] [Info] Start training from score -1.353538
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, bes

[I 2025-02-06 23:37:52,656] Trial 49 finished with value: 0.6541783393428975 and parameters: {'max_depth': 6, 'num_leaves': 138, 'min_child_samples': 150, 'subsample': 0.5113426038370541, 'colsample_bytree': 0.7008963475866742, 'learning_rate': 0.019017523571850256, 'n_estimators': 580, 'reg_alpha': 8.518712072983785, 'reg_lambda': 2.3360975959901995}. Best is trial 32 with value: 0.655607996425505.


Fold 10 - F1-score: 0.6606
[LightGBM] [Info] Number of positive: 28325, number of negative: 109647
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003341 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1235
[LightGBM] [Info] Number of data points in the train set: 137972, number of used features: 17
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.205295 -> initscore=-1.353521
[LightGBM] [Info] Start training from score -1.353521
✅ Modèle optimisé sauvegardé


KeyError: "['HasBalance', 'AgeByBalance', 'BalanceMinusEstimatedSalary', 'BalanceToSalaryRatio', 'AgeByProducts', 'IsHighBalance', 'IsSenior', 'IsActive_by_CreditCard', 'Products_Per_Tenure', 'AgeCat'] not in index"